# Objetivo 

- A partir das máscaras de núvem das imagens do sentinel 2 
 

Gerar um gpkg a partir do raster 

começando para o dia 09/09/2022

In [19]:
import rasterio
import numpy as np
import geopandas as gpd
from rasterio.features import shapes
from shapely.geometry import shape

# Função para reclassificar o raster
def reclassify_raster(input_raster, output_raster):
    with rasterio.open(input_raster) as src:
        data = src.read(1)
        meta = src.meta

        # Reclassificando valores
        reclassified_data = np.where(np.isin(data, [2, 3, 4, 5, 6]), 1, 0)

        # Atualizando o metadado para o raster de saída
        meta.update(dtype=rasterio.uint8, count=1)

        with rasterio.open(output_raster, 'w', **meta) as dst:
            dst.write(reclassified_data, 1)

# Função para converter raster para vetor e transformar coordenadas
def raster_to_vector(raster_path, vector_path):
    with rasterio.open(raster_path) as src:
        # Criar uma máscara para os pixels onde o valor é 1
        mask = (src.read(1) == 1)

        # Criar um conjunto de polígonos a partir da máscara
        shapes_gen = shapes(src.read(1), mask=mask, transform=src.transform)
        geoms = [shape(geom) for geom, value in shapes_gen if value == 1]

        # Filtrar geometrias válidas
        valid_geoms = [geom for geom in geoms if geom.is_valid]

        # Criar um GeoDataFrame
        gdf = gpd.GeoDataFrame(geometry=valid_geoms, crs=src.crs)

        # Dissolver os polígonos
        dissolved = gdf.dissolve()

        # Transformar as coordenadas para EPSG:4326
        dissolved = dissolved.to_crs(epsg=4326)

        # Salvar o GeoDataFrame como shapefile
        dissolved.to_file(vector_path)

# Caminhos dos arquivos
input_raster = '09-09/S2A_SCL_20220909T133201_N0400_R081_T22LHH_20220909T202800.tif'  # insira o caminho para o seu raster
reclassified_raster = '09-09/S2A_SCL_20220909T133201_N0400_R081_T22LHH_20220909T202800_sample.tif'
output_vector = '09-09/S2A_SCL_20220909T133201_N0400_R081_T22LHH_20220909T202800_sample.shp'

# Executar as funções
reclassify_raster(input_raster, reclassified_raster)
raster_to_vector(reclassified_raster, output_vector)

print("Processamento concluído!")


Processamento concluído!


# Agora repetindo para o dia 14/09/2022

In [21]:
# Caminhos dos arquivos
path = '14-09/S2B_SCL_20220914T133149_N0400_R081_T22LHH_20220914T154942'
input_raster = f'{path}.tif'  # insira o caminho para o seu raster
reclassified_raster = f'{path}_new_cut.tif'
output_vector = f'{path}_new_cut.shp'

# Executar as funções
reclassify_raster(input_raster, reclassified_raster)
raster_to_vector(reclassified_raster, output_vector)

print("Processamento concluído!")

Processamento concluído!


# Agora Repetindo para o dia 04/09/2022

In [23]:
# Caminhos dos arquivos
path = '04-09/S2B_SCL_20220904T133149_N0400_R081_T22LHH_20220904T154537'
input_raster = f'{path}.tif'  # insira o caminho para o seu raster
reclassified_raster = f'{path}_new_cut.tif'
output_vector = f'{path}_new_cut.shp'

# Executar as funções
reclassify_raster(input_raster, reclassified_raster)
raster_to_vector(reclassified_raster, output_vector)

print("Processamento concluído!")

Processamento concluído!


# Agora Repetindo para o dia 19/09/2022

In [8]:
# Caminhos dos arquivos
path = '19_09/S2A_SCL_20220919T133151_N0400_R081_T22LHH_20220919T203359'
input_raster = f'{path}.tif'  # insira o caminho para o seu raster
reclassified_raster = f'{path}_cut.tif'
output_vector = f'{path}_cut.shp'

# Executar as funções
reclassify_raster(input_raster, reclassified_raster)
raster_to_vector(reclassified_raster, output_vector)

print("Processamento concluído!")

Processamento concluído!


# Agora Repetindo para o dia 24/09/2022

In [20]:
# Caminhos dos arquivos
path = '24-09/S2B_SCL_20220924T133149_N0400_R081_T22LHH_20220924T154251'
input_raster = f'{path}.tif'  # insira o caminho para o seu raster
reclassified_raster = f'{path}_new_cut.tif'
output_vector = f'{path}_new_cut.shp'

# Executar as funções
reclassify_raster(input_raster, reclassified_raster)
raster_to_vector(reclassified_raster, output_vector)

print("Processamento concluído!")

Processamento concluído!


# Agora Repetindo para o dia 29/09/2022

In [22]:
# Caminhos dos arquivos
path = '29-09/S2A_SCL_20220929T133151_N0400_R081_T22LHH_20220929T182656'
input_raster = f'{path}.tif'  # insira o caminho para o seu raster
reclassified_raster = f'{path}_new_cut.tif'
output_vector = f'{path}_new_cut.shp'

# Executar as funções
reclassify_raster(input_raster, reclassified_raster)
raster_to_vector(reclassified_raster, output_vector)

print("Processamento concluído!")

Processamento concluído!


# Agora para poder fazer o dnbr as máscaras tem que ser as mesmas. 

DEssa forma teremos que usar a máscara de nbr para tanto a data atual como para a data anterior dessa forma estou fazendo um intersect entre as duas máscaras 

## Como before o dia 04/09/2022

DEssa forma temos a seguinte lógica a empregar quando a data for before então utilizaremos a segunte nomenclatura dentor da pasta *asbefore*  caso seja após a queimada será denominada como *asafter* dessa forma tirando a última data e a primeira todas as demais teram um arquivo *asbefore* e um *asafter*

- dessa lógica o intersect será entre duas máscaras de núvem considerando os píxeis 2,3,4,5,6,7 da SCL 
- A data inícial da série histórica considerada somente conta com o arquivo *asbefore* 
- A data Final da série histórica considerada somente conta com o arquivo *asafter*
- As demais datas contam tanto com um arquivo *asbefore* quanto com um *asafter*

In [2]:
# Primeira data vou colocar aqui tanto os caminhos 

import geopandas as gpd

# Carregar os shapefiles
shapefile1 = gpd.read_file('04-09/S2B_SCL_20220904T133149_N0400_R081_T22LHH_20220904T154537_cut.shp')
shapefile2 = gpd.read_file('09_09/S2A_SCL_20220909T133201_N0400_R081_T22LHH_20220909T202800_sample.shp')

# Verificar CRS
if shapefile1.crs != shapefile2.crs:
    # Reprojetar shapefile2 para o CRS de shapefile1
    shapefile2 = shapefile2.to_crs(shapefile1.crs)

# Realizar a interseção
intersected = gpd.overlay(shapefile1, shapefile2, how='intersection')

# Salvar o resultado em um novo shapefile
intersected.to_file('04-09/asbefore.shp')
intersected.to_file('09-09/asafter.shp')

print("Interseção realizada com sucesso e coordenadas preservadas!")


Interseção realizada com sucesso e coordenadas preservadas!


In [8]:
data_before = '09'
data_after = '14'

file_before = '09_09/S2A_SCL_20220909T133201_N0400_R081_T22LHH_20220909T202800_sample.shp'
file_after = '14-09/S2B_SCL_20220914T133149_N0400_R081_T22LHH_20220914T154942_cut.shp'

def intersect_dates(data_before = '09_', data_after = '14-', file_before = '09_09/S2A_SCL_20220909T133201_N0400_R081_T22LHH_20220909T202800_sample.shp',file_after = '14-09/S2B_SCL_20220914T133149_N0400_R081_T22LHH_20220914T154942_cut.shp'):
    import geopandas as gpd

    # Carregar os shapefiles
    shapefile1 = gpd.read_file(f'{file_before}')
    shapefile2 = gpd.read_file(f'{file_after}')

    # Verificar CRS
    if shapefile1.crs != shapefile2.crs:
        # Reprojetar shapefile2 para o CRS de shapefile1
        shapefile2 = shapefile2.to_crs(shapefile1.crs)

    # Realizar a interseção
    intersected = gpd.overlay(shapefile1, shapefile2, how='intersection')

    # Salvar o resultado em um novo shapefile
    intersected.to_file(f'{data_before}09/asbefore.shp')
    intersected.to_file(f'{data_after}09/asafter2.shp')

    print("Interseção realizada com sucesso e coordenadas preservadas!")


# data_before = '19_'
# data_after =  '24-'


# file_before = '19_09/S2A_SCL_20220919T133151_N0400_R081_T22LHH_20220919T203359_cut.shp'
# file_after = '24-09/S2B_SCL_20220924T133149_N0400_R081_T22LHH_20220924T154251_cut.shp'
# intersect_dates(data_before,data_after,file_before,file_after)

#intersect_dates(data_before,data_after,file_before,file_after)

In [5]:
data_before = '14-'
data_after = '19_'


file_before = '14-09/S2B_SCL_20220914T133149_N0400_R081_T22LHH_20220914T154942_cut.shp'
file_after = '19_09/S2A_SCL_20220919T133151_N0400_R081_T22LHH_20220919T203359_cut.shp'

intersect_dates(data_before,data_after,file_before,file_after)

Interseção realizada com sucesso e coordenadas preservadas!


/tmp/ipykernel_187227/707079615.py:20: UserWarning: `keep_geom_type=True` in overlay resulted in 676 dropped geometries of different geometry types than df1 has. Set `keep_geom_type=False` to retain all geometries
  intersected = gpd.overlay(shapefile1, shapefile2, how='intersection')


In [4]:
data_before = '19_'
data_after =  '24-'


file_before = '19_09/S2A_SCL_20220919T133151_N0400_R081_T22LHH_20220919T203359_cut.shp'
file_after = '24-09/S2B_SCL_20220924T133149_N0400_R081_T22LHH_20220924T154251_cut.shp'
intersect_dates(data_before,data_after,file_before,file_after)

Interseção realizada com sucesso e coordenadas preservadas!


/tmp/ipykernel_208085/3585881080.py:20: UserWarning: `keep_geom_type=True` in overlay resulted in 1391 dropped geometries of different geometry types than df1 has. Set `keep_geom_type=False` to retain all geometries
  intersected = gpd.overlay(shapefile1, shapefile2, how='intersection')


In [24]:
data_before = '04-'
data_after =  '29-'


file_before = '04-09/S2B_SCL_20220904T133149_N0400_R081_T22LHH_20220904T154537_new_cut.shp'
file_after = '29-09/S2A_SCL_20220929T133151_N0400_R081_T22LHH_20220929T182656_new_cut.shp'
intersect_dates(data_before,data_after,file_before,file_after)

Interseção realizada com sucesso e coordenadas preservadas!


/tmp/ipykernel_60753/1088831885.py:20: UserWarning: `keep_geom_type=True` in overlay resulted in 1266 dropped geometries of different geometry types than df1 has. Set `keep_geom_type=False` to retain all geometries
  intersected = gpd.overlay(shapefile1, shapefile2, how='intersection')


# Geração do dNBR

para gerar o dnbr eu preciso aplicar a máscara de nuvem do as before na data anterior e do as after na data posterior essa máscara é a mesma porem salva em datas diferentes dessa forma eu posso economizar memória somente chamando uma máscara que é a máscara da diferença entre as duas variáveis 

In [23]:
import rasterio
with rasterio.open('19_09/dNBR.tif') as src:
    array = src.read(1)
    

In [31]:
import numpy as np
import geopandas as gpd
import rasterio
from rasterio.mask import mask
from shapely.geometry import box

# Caminhos para as bandas e shapefile
caminho_nir = '29-09/S2A_B12_20220929T133151_N0400_R081_T22LHH_20220929T182656.tif'
caminho_swir = '29-09/S2A_B8A_20220929T133151_N0400_R081_T22LHH_20220929T182656.tif'
caminho_shapefile = '29-09/asafter2.shp'

# Carregar o shapefile
poligono = gpd.read_file(caminho_shapefile)

# Lê o raster e obtém seu CRS
with rasterio.open(caminho_nir) as src_nir:
    raster_crs = src_nir.crs
    raster_bounds = src_nir.bounds  # Obter os limites do raster

# Reprojetar o polígono se necessário
if poligono.crs != raster_crs:
    poligono = poligono.to_crs(raster_crs)

# Criar um polígono a partir dos limites do raster
raster_polygon = box(*raster_bounds)

# Verificação de sobreposição
if not poligono.intersects(raster_polygon).any():
    raise ValueError("O polígono não se sobrepõe à extensão do raster.")

# Lê as bandas usando rasterio e aplica a máscara
with rasterio.open(caminho_nir) as src_nir:
    out_nir, out_transform = mask(src_nir, poligono.geometry, crop=True)

with rasterio.open(caminho_swir) as src_swir:
    out_swir, _ = mask(src_swir, poligono.geometry, crop=True)

# Calcula o NBR apenas na região da máscara
nbr = (out_nir - out_swir) / (out_nir + out_swir)

# Remover dimensões extras
nbr = nbr.squeeze()

# Salva o NBR em um novo arquivo TIFF
meta = src_nir.meta  # Use os metadados do primeiro raster
meta.update(dtype=rasterio.float32, count=1, height=nbr.shape[0], width=nbr.shape[1])

with rasterio.open('29-09/nbr_new_large.tif', 'w', **meta) as dst:
    dst.write(nbr.astype(rasterio.float32), 1)

print("Cálculo do NBR concluído e salvo em '29_09/nbr_new_large.tif'")


/tmp/ipykernel_60753/1881106526.py:39: RuntimeWarning: invalid value encountered in divide
  nbr = (out_nir - out_swir) / (out_nir + out_swir)


Cálculo do NBR concluído e salvo em '29_09/nbr_new_large.tif'


In [5]:
import geopandas as gpd

# Carregue os dados
event_fire = gpd.read_file('EVENT_FIRE.gpkg')
areas_queimadas = gpd.read_file('29-09/areas_queimadas_large_difference.shp')
# Filtrar os polígonos de event_fire que tocam em areas_queimadas
toques = event_fire[event_fire.geometry.touches(areas_queimadas.unary_union)]

# Unir todos os polígonos que tocam
poligono_unido = toques.unary_union

# Criar uma lista de geometrias separadas se for GeometryCollection
if poligono_unido.geom_type == 'GeometryCollection':
    geometries = [geom for geom in poligono_unido.geoms]
else:
    geometries = [poligono_unido]

# Criar um GeoDataFrame com geometrias separadas
gdf_resultado = gpd.GeoDataFrame(geometry=geometries, crs=event_fire.crs)

# Garantir que todas as geometrias são do tipo Polygon ou MultiPolygon
gdf_resultado = gdf_resultado[gdf_resultado.geometry.type.isin(['Polygon', 'MultiPolygon'])]

# Verifique se gdf_resultado não está vazio
if gdf_resultado.empty:
    raise ValueError("Nenhuma geometria válida para salvar.")

# Salvar como um shapefile
gdf_resultado.to_file('poligono_touches.shp')




/tmp/ipykernel_341824/409205533.py:7: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  toques = event_fire[event_fire.geometry.touches(areas_queimadas.unary_union)]
/tmp/ipykernel_341824/409205533.py:10: DeprecationWarning: The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.
  poligono_unido = toques.unary_union


ValueError: Nenhuma geometria válida para salvar.

In [26]:
import numpy as np
import geopandas as gpd
import rasterio
from rasterio.mask import mask
from shapely.geometry import box

# Caminhos para as bandas e shapefile
path='20220904T133149_N0400_R081_T22LHH_20220904T154537'
caminho_nir = f'04-09/S2B_B12_{path}.tif'
caminho_swir = f'04-09/S2B_B8A_{path}.tif'
caminho_shapefile = '04-09/asbefore.shp'

# Carregar o shapefile
poligono = gpd.read_file(caminho_shapefile)

# Lê o raster e obtém seu CRS
with rasterio.open(caminho_nir) as src_nir:
    raster_crs = src_nir.crs
    raster_bounds = src_nir.bounds  # Obter os limites do raster

# Reprojetar o polígono se necessário
if poligono.crs != raster_crs:
    poligono = poligono.to_crs(raster_crs)

# Criar um polígono a partir dos limites do raster
raster_polygon = box(*raster_bounds)

# Verificação de sobreposição
if not poligono.intersects(raster_polygon).any():
    raise ValueError("O polígono não se sobrepõe à extensão do raster.")

# Lê as bandas usando rasterio e aplica a máscara
with rasterio.open(caminho_nir) as src_nir:
    out_nir, out_transform = mask(src_nir, poligono.geometry, crop=True)

with rasterio.open(caminho_swir) as src_swir:
    out_swir, _ = mask(src_swir, poligono.geometry, crop=True)

# Calcula o NBR apenas na região da máscara
nbr = (out_nir - out_swir) / (out_nir + out_swir)

# Remover dimensões extras
nbr = nbr.squeeze()

# Salva o NBR em um novo arquivo TIFF
meta = src_nir.meta  # Use os metadados do primeiro raster
meta.update(dtype=rasterio.float32, count=1, height=nbr.shape[0], width=nbr.shape[1])

with rasterio.open('04-09/nbr_new.tif', 'w', **meta) as dst:
    dst.write(nbr.astype(rasterio.float32), 1)

print("Cálculo do NBR concluído e salvo em '04-09/nbr_new_.tif'")


/tmp/ipykernel_60753/1239092500.py:40: RuntimeWarning: invalid value encountered in divide
  nbr = (out_nir - out_swir) / (out_nir + out_swir)


Cálculo do NBR concluído e salvo em '04-09/nbr_new_.tif'


In [29]:
import rasterio
import numpy as np
import geopandas as gpd
from shapely.geometry import box
from rasterio.features import shapes
from rasterio.enums import Resampling

# Abrir os rasters
raster2_path = '29-09/nbr_new.tif'
raster1_path = '04-09/nbr_new.tif'

with rasterio.open(raster1_path) as src1:
    # Ler os dados do raster 1
    data1 = src1.read(1)
    transform1 = src1.transform
    
    # Obter os metadados para o raster de saída
    meta = src1.meta.copy()

with rasterio.open(raster2_path) as src2:
    # Reamostrar o raster 2 para coincidir com o raster 1
    data2 = src2.read(1, out_shape=(1, meta['height'], meta['width']),
                      resampling=Resampling.bilinear)
    
    # Ajustar a transformação para o novo raster
    transform2 = src2.transform * src2.transform.scale(
        (src2.width / meta['width']),
        (src2.height / meta['height'])
    )

# Fazer a subtração
result = data1 - data2

# Criar uma máscara para áreas queimadas
burned_mask = (result > 10.1).astype(np.uint8)  # Convertendo para uint8 para shapes

# Extrair polígonos usando rasterio.features
results = (
    {'properties': {'burned': 1}, 'geometry': geom}
    for geom, value in shapes(burned_mask, mask=burned_mask, transform=transform1) if value == 1
)

# Criar um GeoDataFrame
gdf = gpd.GeoDataFrame.from_features(list(results), crs=src1.crs)

# Garantir que o GeoDataFrame tenha a mesma extensão do raster
gdf['geometry'] = gdf.geometry.apply(lambda geom: geom.intersection(box(*src1.bounds)) if not geom.is_empty else geom)

# Salvar como shapefile
gdf.to_file('29-09/areas_queimadas_large_difference.shp')


In [1]:
import geopandas as gpd
from shapely.geometry import MultiPoint

# Ler o polígono do shapefile
shapefile_path = '29-09/asafter2.shp'
poligono_gdf = gpd.read_file(shapefile_path)

# Supondo que o shapefile tenha uma única geometria
poligono = poligono_gdf.geometry.iloc[0]  # Pega o primeiro polígono

# Ler o MultiPoint do GeoPackage
gpkg_path = 'FOCOS_SETEMBRO_2022.gpkg'
multipo_gdf = gpd.read_file(gpkg_path)

# Convertendo para MultiPoint, se necessário
multi_points = MultiPoint(multipo_gdf.geometry.tolist())

# Verificação
print("Polígono:", poligono)
print("MultiPoint:", multi_points)


Polígono: MULTIPOLYGON (((-48.18100916628214 -16.3503794213006, -48.18194432955874 -16.350391919517246, -48.181946919867784 -16.35021143753041, -48.181011757674376 -16.350198923690996, -48.18100916628214 -16.3503794213006)), ((-48.19283197223623 -16.30845323283519, -48.19264498357888 -16.308450746318734, -48.192642408621545 -16.30863133110399, -48.192829397222354 -16.308633817646452, -48.19283197223623 -16.30845323283519)), ((-48.19264498357888 -16.308450746318734, -48.19264755850375 -16.308270161529993, -48.19264755499358 -16.308270161483314, -48.19264497998744 -16.30845074627097, -48.19264498357888 -16.308450746318734)), ((-48.19675615071066 -16.03052910335371, -48.19677634929601 -16.029084382230593, -48.19658966356052 -16.02908194108695, -48.196569463376214 -16.03052666197519, -48.19675615071066 -16.03052910335371)), ((-48.19677887411936 -16.028903792076697, -48.196786448589684 -16.028362021597015, -48.196599762878805 -16.02835958056068, -48.196592188438466 -16.028901350960517, -48.

/home/danielfarkat/miniconda3/envs/meu_ambiente/lib/python3.9/site-packages/pyogrio/raw.py:198: RuntimeWarning: Non-conformant content for record 250 in column data_hora_gmt, 2022-09-02T17:17:00.000-03:00, successfully parsed
  return ogr_read(


In [2]:
import geopandas as gpd
from shapely.geometry import MultiPoint

# Ler o polígono do shapefile
shapefile_path = '29-09/asafter2.shp'
poligono_gdf = gpd.read_file(shapefile_path)

# Supondo que o shapefile tenha uma única geometria
poligono = poligono_gdf.geometry.iloc[0]  # Pega o primeiro polígono

# Ler o MultiPoint do GeoPackage
gpkg_path = 'FOCOS_SETEMBRO_2022.gpkg'
multipo_gdf = gpd.read_file(gpkg_path)
# Convertendo para MultiPoint
multi_points = MultiPoint(multipo_gdf.geometry.tolist())

# Verificar se algum ponto do MultiPoint está dentro do polígono
# Crie uma nova coluna para armazenar o resultado
multipo_gdf['dentro_do_poligono'] = multipo_gdf.geometry.apply(lambda ponto: ponto.intersects(poligono))

# Filtrar apenas os pontos que estão dentro do polígono
pontos_dentro = multipo_gdf[multipo_gdf['dentro_do_poligono']]

if not pontos_dentro.empty:
    print("Pelo menos um ponto do MultiPoint está dentro do polígono.")
    
    # Salvar os pontos que estão dentro do polígono em um novo arquivo
    pontos_dentro.to_file('intersect_with_firespot.shp', driver='ESRI Shapefile')
else:
    print("Nenhum ponto do MultiPoint está dentro do polígono.")


/home/danielfarkat/miniconda3/envs/meu_ambiente/lib/python3.9/site-packages/pyogrio/raw.py:198: RuntimeWarning: Non-conformant content for record 250 in column data_hora_gmt, 2022-09-02T17:17:00.000-03:00, successfully parsed
  return ogr_read(


Pelo menos um ponto do MultiPoint está dentro do polígono.


/tmp/ipykernel_2693/174884152.py:28: UserWarning: Column names longer than 10 characters will be truncated when saved to ESRI Shapefile.
  pontos_dentro.to_file('intersect_with_firespot.shp', driver='ESRI Shapefile')
/home/danielfarkat/miniconda3/envs/meu_ambiente/lib/python3.9/site-packages/pyogrio/raw.py:723: RuntimeWarning: Normalized/laundered field name: 'id_foco_bdq' to 'id_foco_bd'
  ogr_write(
/home/danielfarkat/miniconda3/envs/meu_ambiente/lib/python3.9/site-packages/pyogrio/raw.py:723: RuntimeWarning: Normalized/laundered field name: 'data_hora_gmt' to 'data_hora_'
  ogr_write(
/home/danielfarkat/miniconda3/envs/meu_ambiente/lib/python3.9/site-packages/pyogrio/raw.py:723: RuntimeWarning: Field data_hora_ create as date field, though DateTime requested.
  ogr_write(
/home/danielfarkat/miniconda3/envs/meu_ambiente/lib/python3.9/site-packages/pyogrio/raw.py:723: RuntimeWarning: Normalized/laundered field name: 'precipitacao' to 'precipitac'
  ogr_write(
/home/danielfarkat/minico